In [12]:
## OPTIMISTIC INITIAL VALUES

import numpy as np
import matplotlib.pyplot as plt
import time
%matplotlib inline

### FUNCIONES A NIVEL MODULO
global start_timer
start_timer = time.time()

def GenerarMazo():
    #Formato Cartas ID, Nombre, ValorTruco
    #Solucion final sera con 9 cartas (reduce statespace y permite codificar en base 10) tomadas al azar de las 40
    Carta.ResetContCarta()
    MAZO = []
    MAZO.append(Carta("4-Copa", 10))
    MAZO.append(Carta("6-Copa", 20))
    MAZO.append(Carta("6-Basto", 20))
    MAZO.append(Carta("11-Copa", 30))
    MAZO.append(Carta("11-Basto", 30))
    MAZO.append(Carta("2-Copa", 40))
    MAZO.append(Carta("2-Basto", 40))       
    MAZO.append(Carta("1-Basto", 80))
    MAZO.append(Carta("1-Espada", 100))
    return  MAZO

def GenerarAcciones():
    # podrian ser "carta mas alta, media y baja en puntaje?", pero y si son todas absolutamente altas?
    # codificar la carta a jugar (accion) con base en un feature (puntaje relativo) parece suboptimo
    # usar puntaje absoluto implicaria demasiadas acciones posibles quedandome un SxA ya demasiado alto
    # Pareceria que cada accion/carta necesitaria un feature set mas amplio y una "activacion" no lineal
    ACCIONES = {}
    ACCIONES[1] = "Jugar Carta 1"
    ACCIONES[2] = "Jugar Carta 2"
    ACCIONES[3] = "Jugar Carta 3"
    return ACCIONES


def GetHashCode_de_Estado():
    result = ""
    for i in cartas_jugadas:
        result = result + str(i.ID)        
    for j in range(6-len(cartas_jugadas)):
        result = result + "0"
    return int(result)
    
def LoadEstado_FromHash(codigoHash, debug=False):
    #agregar if estado !=0
    unE = Estado()
    unE.cartas_jugadas = []

    for c in str(codigoHash):
        if debug : printDebug("caracter: " + c)
        if (int(c)>0): 
            unE.cartas_jugadas.append(Reglas.MAZO[int(c)-1])
            if debug : printDebug("estado: " + str(unE))
    return unE

def GetAllStates(debug=False):
    results = []
    for j in GetAllStatesCodes(Reglas.MAZO[:], 6):
        unE = Estado()
        if debug : printDebug("state code: " + j)
        unE = LoadEstado_FromHash(j)
        if debug : printDebug("estado: " + str(unE))
        results.append(unE)    
    return results   

def GetAllStatesCodes(mazoRestante, jugadasRestantes, debug=False):
    results = []
    
    #Caso Base:
    if(jugadasRestantes == 1):
        for ultima_carta in mazoRestante: 
            if debug : printDebug("caso terminal: " + str(ultima_carta.ID))
            results.append(ultima_carta.ID)
        results.append("0")
    else:
    #Caso Recursivo, 2 o mas digitos que debo devolver
        for j in mazoRestante[:]: #Para cada carta en el mazo, va de 1 a N 
            if debug : printDebug("Comienzo con carta:" + str(j.ID) + " de:" + str(len(mazoRestante)))
            mazoRestante.remove(j)
            for k in GetAllStatesCodes(mazoRestante[:],jugadasRestantes-1): 
                if debug : printDebug("pase por aca 3, k=" + str(k) + " mazorestante:" + str(len(mazoRestante)))
                unCode = str(j.ID) + str(k)
                if debug : printDebug("Agrego a mi retorno: " + unCode)
                results.append(unCode)
            mazoRestante.append(j) #retorno la carta que habia quitado al mazo antes de continuar con la siguiente carta
        
        #Falta el caso de que aqui va un 0 (y por lo tanto fuerzo completar con ceros)
        unCode = ""
        for padding in range(jugadasRestantes):
            unCode = unCode + "0"
        results.append(unCode)            
            
    return results     

def printDebug(debugMsg):
    print("   #debug: " +debugMsg+ " ## T=" + str(time.time() - start_timer)[0:7] + "s", flush=True);
    return;

class Carta:
    cont_interno = 0
    def __init__(self, Nombre, ValorTruco):
        Carta.cont_interno += 1
        self.ID = Carta.cont_interno
        self.Nombre = Nombre
        self.ValorTruco = ValorTruco    
    def __repr__(self): 
        #override print() oupput a consola
        return ("ID:" + str(self.ID) + ", carta: " + self.Nombre + ", valorTruco:" + str(self.ValorTruco))
    def __str__(self): #python
        #override del str()
        return ("ID:" + str(self.ID) + ", carta: " + self.Nombre + ", valorTruco:" + str(self.ValorTruco))
    def ResetContCarta():
        Carta.cont_interno = 0
        
class Reglas:
    
    MAZO = GenerarMazo()
    ACCIONES = GenerarAcciones()
    JUGADOR1 = 1
    JUGADOR2 = 2    
    
    def PuntosEvidos(carta1, carta2, carta3):
        #TODO, para hacer luego, pero dejo el metodo  para mostrar que va aca
        assert(False) #Not implmented yet
        return None

class Estado:
    #el estado actual, episodio podria llevar lista de estados y acciones
    #Contiene las cartas que se jugaron, si ya se dijo envido y el estado del truco (quien tiene la palabra)
    #sabe decir a quien le toca
    
    def __init__(self):
        self.cartas_jugadas = []
        #self.palabraTruco = Reglas.JUGADOR1
        #self.palabraEnvido = Reglas.JUGADOR1
        # TRUCO, valores posibles:
        # 0-No se dijo nada, 1-Truco Dicho, 2-Truco aceptado, 3-Truco rechazado, 4-Retruco echado
        # 4-Retruco echado, 5-Retruco aceptado, 6-Retruco rechazado
        # 7-ValeCuatro echado, 8-ValeCuatro aceptado, 9-ValeCuatro rechazado
        # self.truco = 0

    
    def QuienGano(self):
        puntos_j1 = 0
        puntos_j2 = 0
        cartas_jugadas = self.cartas_jugadas
        
        if (len(cartas_jugadas) != 6 or len(cartas_jugadas) != 4 ):
            return None
        
        if (cartas_jugadas[0].ValorTruco > cartas_jugadas[1].ValorTruco):
            puntos_j1 += 1
        elif (cartas_jugadas[0].ValorTruco < cartas_jugadas[1].ValorTruco):
            puntos_j2 += 1
        if (cartas_jugadas[2].ValorTruco > cartas_jugadas[3].ValorTruco):
            puntos_j1 += 1
        elif (cartas_jugadas[2].ValorTruco < cartas_jugadas[3].ValorTruco):
            puntos_j2 += 1
        if (cartas_jugadas[4].ValorTruco > cartas_jugadas[5].ValorTruco):
            puntos_j1 += 1
        elif (cartas_jugadas[4].ValorTruco < cartas_jugadas[5].ValorTruco):
            puntos_j2 += 1
        
        if (puntos_j1 > puntos_j2):
            return Reglas.JUGADOR1
        elif (puntos_j1 < puntos_j2):
            return Reglas.JUGADOR2
        else:
            return None
    
    def Dibujar_Estado_Consola(self):
        print(cartas_jugadas)
    
    def QuienLeToca():
        cartas_jugadas = self.cartas_jugadas
        
        #Estamos en primera Mano
        if (len(cartas_jugadas)==0):
            return Reglas.JUGADOR1          
        if (len(cartas_jugadas)==1):
            return Reglas.JUGADOR2
        
        #En 2da mano
        if (len(cartas_jugadas)==2 or len(cartas_jugadas)==3):
            if (cartas_jugadas[0].ValorTruco >= cartas_jugadas[1].ValorTruco):
                return Reglas.JUGADOR1   
            if (cartas_jugadas[0].ValorTruco < cartas_jugadas[1].ValorTruco):
                return Reglas.JUGADOR2
        #En 3ra mano  
        if (len(cartas_jugadas)==3 or len(cartas_jugadas)==4):
            if (cartas_jugadas[2].ValorTruco >= cartas_jugadas[3].ValorTruco):
                return Reglas.JUGADOR1   
            if (cartas_jugadas[2].ValorTruco < cartas_jugadas[3].ValorTruco):
                return Reglas.JUGADOR2  
            
        return None
    
    def __repr__(self): 
        #override print() oupput a consola
        return ("cartas jugadas:" + str(len(cartas_jugadas))  +str(cartas_jugadas))
    def __str__(self): #python
        #override del str()
        return ("cartas jugadas:" + str(len(cartas_jugadas))  +str(cartas_jugadas))
    
    
class Episodio:    
    def __init__(self):
        self.lista_manos = []
        self.lista_acciones = []

        
class Agente:
    def __init__(self, jugador, eps=0.1, alpha=0.5, verbose=False):
        self.eps = eps # probability of choosing random action instead of greedy
        self.alpha = alpha # learning rate
        self.gamma = 0.9 # discount factor
        self.verbose = False
        self.state_history = []
        self.Q = {}
        if(jugador == Reglas.JUGADOR1):
            self.jugador = Reglas.JUGADOR1
        elif (jugador == Reglas.JUGADOR2):
            self.jugador = Reglas.JUGADOR2
        elif (jugador != self.jugador):
            self.jugador = None
            assert(self.jugador!=None)
    
    def Tomar_Accion(self):
        return None
    
    def InicializarQ():
        # initialize Q(s,a)
        self.Q = {}
        
    
    
class Humano:    
    def __init__(self, mano):
        self.mano = mano
    def Tomar_Accion(self):
        return None
    

In [13]:
#PRUEBAS GENERALES ENTIDADES
Reglas = Reglas()
print(Reglas.MAZO)
print(Reglas.ACCIONES)
c1 = Carta("Carta A", 10)
print(c1)
str(c1)
a1 = Agente(Reglas.JUGADOR2)
print(a1.jugador)
#a2 = Agente("123") #a ver si da error como debe
a3 = Agente(Reglas.JUGADOR1)
a4 = Agente(Reglas.JUGADOR2)
e1 = Estado()
print(e1.QuienGano())

[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:4, carta: 11-Copa, valorTruco:30, ID:5, carta: 11-Basto, valorTruco:30, ID:6, carta: 2-Copa, valorTruco:40, ID:7, carta: 2-Basto, valorTruco:40, ID:8, carta: 1-Basto, valorTruco:80, ID:9, carta: 1-Espada, valorTruco:100]
{1: 'Jugar Carta 1', 2: 'Jugar Carta 2', 3: 'Jugar Carta 3'}
ID:10, carta: Carta A, valorTruco:10
2
None


In [14]:
# PRUEBA HASH
Carta.ResetContCarta()
cartas_jugadas = []


cartas_jugadas.append(Carta("6-Copa", 10))
cartas_jugadas.append(Carta("6-Basto", 10))

result = ""
for i in cartas_jugadas:
    result = result + str(i.ID)    
for j in range(6-len(cartas_jugadas)):
    result = result + "0"    
printDebug("codigo levantado:  " + str(int(result)))


# PRUEBA RECONSTRUCCION DESDE UN HASH
Carta.ResetContCarta()
Reglas.MAZO = GenerarMazo()
printDebug("total cartas en MAZO: " + str(len(Reglas.MAZO)))
print(str(Reglas.MAZO))
cartas_jugadas = []
idEstado = "123740"
printDebug("Hashcode a Levantar: " + str(idEstado))

for c in str(idEstado):
    if (int(c)>0): 
        cartas_jugadas.append(Reglas.MAZO[int(c)-1])
print(cartas_jugadas)

Carta.ResetContCarta()
Reglas.MAZO = GenerarMazo()
idEstado = "123740"
printDebug("total cartas en MAZO: " + str(len(Reglas.MAZO)))
printDebug("Hashcode a Levantar: " + str(idEstado))
    
unE = LoadEstado_FromHash(idEstado)
printDebug("ESTADO LEVANTADO: " + str((unE.cartas_jugadas)))

   #debug: codigo levantado:  120000 ## T=1.56219s
   #debug: total cartas en MAZO: 9 ## T=1.56319s
[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:4, carta: 11-Copa, valorTruco:30, ID:5, carta: 11-Basto, valorTruco:30, ID:6, carta: 2-Copa, valorTruco:40, ID:7, carta: 2-Basto, valorTruco:40, ID:8, carta: 1-Basto, valorTruco:80, ID:9, carta: 1-Espada, valorTruco:100]
   #debug: Hashcode a Levantar: 123740 ## T=1.56418s
[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30]
   #debug: total cartas en MAZO: 9 ## T=1.56518s
   #debug: Hashcode a Levantar: 123740 ## T=1.56518s
   #debug: ESTADO LEVANTADO: [ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=1.56618s


In [18]:
#PRUEBA GET ALL STATES CODES
Carta.ResetContCarta()
Reglas.MAZO = GenerarMazo()
algo1 = GetAllStatesCodes(Reglas.MAZO, 4)
algo1.sort()
print("cantidad de codigos posibles: " + str(len(algo1)))
cont = 0
for i in algo1:
    cont = cont +1
    #print(str(cont) + " nro" + str(i)  )
#print(algo)

#PRUEBA GET ALL STATES
Carta.ResetContCarta()
Reglas.MAZO = GenerarMazo()
algo2 = GetAllStates(True) #solo usar cuando este listo el getallstatecodes   
print("cantidad de estados posibles: " + str(len(algo2)))
cont = 0
for i in algo2:
    cont = cont +1
    if((len(i.cartas_jugadas)) == 1):
        print("#" + str(cont) + ", Estado-" + str(i)  )






cantidad de codigos posibles: 3610
   #debug: state code: 123456 ## T=110.759s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.759s
   #debug: state code: 123457 ## T=110.760s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.760s
   #debug: state code: 123458 ## T=110.760s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.761s
   #debug: state code: 123459 ## T=110.762s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Cop

   #debug: state code: 123560 ## T=110.781s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.782s
   #debug: state code: 123578 ## T=110.782s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.782s
   #debug: state code: 123579 ## T=110.783s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.783s
   #debug: state code: 123574 ## T=110.783s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 123687 ## T=110.803s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.803s
   #debug: state code: 123680 ## T=110.803s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.804s
   #debug: state code: 123694 ## T=110.804s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.804s
   #debug: state code: 123695 ## T=110.805s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 123748 ## T=110.824s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.824s
   #debug: state code: 123749 ## T=110.825s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.825s
   #debug: state code: 123740 ## T=110.825s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.826s
   #debug: state code: 123756 ## T=110.826s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 123869 ## T=110.843s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.843s
   #debug: state code: 123864 ## T=110.843s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.844s
   #debug: state code: 123865 ## T=110.844s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=110.844s
   #debug: state code: 123860 ## T=110.844s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

...

   #debug: state code: 985741 ## T=174.909s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.909s
   #debug: state code: 985742 ## T=174.910s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.910s
   #debug: state code: 985743 ## T=174.910s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.911s
   #debug: state code: 985740 ## T=174.911s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 985172 ## T=174.929s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.930s
   #debug: state code: 985173 ## T=174.930s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.930s
   #debug: state code: 985174 ## T=174.931s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.931s
   #debug: state code: 985176 ## T=174.931s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 985210 ## T=174.956s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.957s
   #debug: state code: 985200 ## T=174.957s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.957s
   #debug: state code: 985346 ## T=174.958s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.958s
   #debug: state code: 985347 ## T=174.959s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 985462 ## T=174.980s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.980s
   #debug: state code: 985463 ## T=174.981s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.981s
   #debug: state code: 985460 ## T=174.981s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=174.982s
   #debug: state code: 985471 ## T=174.982s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

   #debug: state code: 986723 ## T=175.002s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=175.003s
   #debug: state code: 986724 ## T=175.003s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=175.003s
   #debug: state code: 986725 ## T=175.004s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Basto, valorTruco:20, ID:7, carta: 2-Basto, valorTruco:40, ID:4, carta: 11-Copa, valorTruco:30] ## T=175.004s
   #debug: state code: 986721 ## T=175.004s
   #debug: estado: cartas jugadas:5[ID:1, carta: 4-Copa, valorTruco:10, ID:2, carta: 6-Copa, valorTruco:20, ID:3, carta: 6-Ba

In [ ]:
print(str(int("0000")))

In [ ]:
def play_game(p1, p2, env, draw=False):
    # loops until the game is over
    current_player = None
    while (env.QuienGano() != None):
        # alternate between players
        # p1 always starts first
        if current_player == p1:
            current_player = p2
        else:
            current_player = p1

        # draw the board before the user who wants to see it makes a move
        """
        if draw:
            if draw == 1 and current_player == p1:
                env.Dibujar_Estado_Consola()
            if draw == 2 and current_player == p2:
                env.Dibujar_Estado_Consola()
        """-+
        # current player makes a move
        current_player.Tomar_Accion(env)

        # update state histories
        state = env.get_state()
        p1.update_state_history(state)
        p2.update_state_history(state)

        if draw:
            env.draw_board()

        # do the value function update
        p1.update(env)
        p2.update(env)

if __name__ == '__main__':
    #Creamos los Agentes
    p1 = Agente(Reglas.JUGADOR1)
    p2 = Agente(Reglas.JUGADOR2)
    
    #Creamos el estado
    env = Estado()
    
    #inicializamos Qs
    p1.InicializarQ()
    p2.InicializarQ()
    


    T = 30000
    for t in range(T):
        if t % 200 == 0:
            print(t)
        play_game(p1, p2, Environment())

    # play human vs. agent
    # do you think the agent learned to play the game well?
    human = Human()
    human.set_symbol(env.x)
    while True:
        p2.set_verbose(True)
        play_game(human, p2, Environment(), draw=1)
        # I made the agent player 1 because I wanted to see if it would
        # select the center as its starting move. If you want the agent
        # to go second you can switch the human and AI.
        answer = input("Play again? [Y/n]: ")
        if answer and answer.lower()[0] == 'n':
            break
